In [ ]:
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        !pip install --upgrade imutils

In [ ]:
!pip install opencv-contrib-python

# **Extract embeddings from face dataset**

In [ ]:
# Importing all necessary packages

from imutils import paths
import numpy as np
import argparse
import imutils
import pickle
import time
import cv2
import os

In [ ]:
# Load face detector

print("Loading face detector...")

protoPath = os.path.sep.join([r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\face_detection_model', 'deploy.prototxt'])
modelPath = os.path.sep.join([r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\face_detection_model', 'res10_300x300_ssd_iter_140000.caffemodel'])

detector = cv2.dnn.readNetFromCaffe(protoPath, modelPath)


# Load face recognizer

print("\nLoading face recognizer...")
embedder = cv2.dnn.readNetFromTorch(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\openface_nn4.small2.v1.t7')

In [ ]:
# Entering paths to our images dataset

print('\nQuantifying faces...')
imagePaths = list(paths.list_images(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Datasets'))

knownEmbeddings = []
knownNames = []

# Total number of faces
total = 0

In [ ]:
# Loop over all image paths

for (i, imagePath) in enumerate(imagePaths):
  print("Processing image {}/{}".format(i + 1, len(imagePaths)))                  # Extract the person name from the image path
  name = imagePath.split(os.path.sep)[-2]

  image = cv2.imread(imagePath)                                                   # Load the image
  image = imutils.resize(image, width=600)                                        # Resize to (600, 600)
  (h, w) = image.shape[:2]                                                        # Store image dimensions
  imageBlob = cv2.dnn.blobFromImage(                                              # Construct a blob from the image
  	cv2.resize(image, (300, 300)), 1.0, (300, 300),
  	(104.0, 177.0, 123.0), swapRB=False, crop=False)

  detector.setInput(imageBlob)                                                    # Face Detector to localize face in an image
  detections = detector.forward()       

  if len(detections) > 0:                                                         # Ensure at least one face was found
    i = np.argmax(detections[0, 0, :, 2])
    confidence = detections[0, 0, i, 2]        

    if (confidence > 0.1):                                                          # Filtering weak detections
      box = detections[0, 0, i, 3:7] * np.array([w, h, w, h])
      (startX, startY, endX, endY) = box.astype("int")
			
      face = image[startY:endY, startX:endX]
      (fH, fW) = face.shape[:2]
			
      if (fW < 20 or fH < 20):
        continue    

      faceBlob = cv2.dnn.blobFromImage(face, 1.0 / 255, (96, 96), (0, 0, 0), 
                                       swapRB=True, crop=False)                   # Create blob

      embedder.setInput(faceBlob)
      vec = embedder.forward()

      knownNames.append(name)                                                     # Append name to list
      knownEmbeddings.append(vec.flatten())                                       # Append flattened embedding to list
      total += 1                                                

In [ ]:
# Save (pickle) the embeddings and the names

print('Serializing {} encodings:\n'.format(total))

data = {'embeddings': knownEmbeddings, 'names': knownNames}                       # Saved as a dictionary/ HashMap
f = open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Output Embeddings\embeddings.pickle', 'wb')
f.write(pickle.dumps(data))                                                       # Stored as a ByteStream
f.close()
print("Serialized {} encodings.\n".format(total))

# **Train the face recognition model**

In [ ]:
pip install -U scikit-learn

In [ ]:
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVC
import argparse
import pickle

In [ ]:
print("Loading face embeddings:\n")
data = pickle.loads(open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Output Embeddings\embeddings.pickle', 'rb').read())
print("Loaded.\n\n")

print("Encoding labels:\n")
le = LabelEncoder()
labels = le.fit_transform(data['names'])
print("\nLabels encoded.\n")

In [ ]:
print("Training model...\n")
recognizer = SVC(C = 1.0, kernel = "linear", probability = True)
recognizer.fit(data["embeddings"], labels)
print("\nModel trained.\n")

In [ ]:
# Save the actual face recognition model
f = open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Trained Models\recognizer.pickle', "wb")
f.write(pickle.dumps(recognizer))
f.close()

# Save the label encoder
f = open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Trained Models\le.pickle', "wb")
f.write(pickle.dumps(le))
f.close()

# **Recognise faces using OpenCV**

In [1]:
from imutils.video import VideoStream
from imutils.video import FPS
import numpy as np
import argparse
import imutils
import pickle
import time
import cv2
import os

In [2]:
# Load our serialized face detector

print("Loading face detector...\n")
protoPath = os.path.sep.join([r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\face_detection_model', 'deploy.prototxt'])
modelPath = os.path.sep.join([r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\face_detection_model', 'res10_300x300_ssd_iter_140000.caffemodel'])
detector = cv2.dnn.readNetFromCaffe(protoPath, modelPath)
print("Loaded face detector.\n")

# Load our serialized face embedding model
print("\nLoading face recognizer...\n")
embedder = cv2.dnn.readNetFromTorch(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\opencv-face-recognition\openface_nn4.small2.v1.t7')
print("Loaded Face Recognizer.\n")

# Load the SVM Model and LabelEncoder
recognizer = pickle.loads(open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Trained Models\recognizer.pickle', "rb").read())
le = pickle.loads(open(r'C:\Users\Yash Umale\Documents\6th Sem\Open Lab\Python Files\Project Files\Trained Models\le.pickle', "rb").read())

Loading face detector...

Loaded face detector.


Loading face recognizer...

Loaded Face Recognizer.



In [3]:
# Initialize the video stream, then allow the camera sensor to warm up

print("Starting video stream...\n")

vs = VideoStream(src = 0).start()
time.sleep(2.0)

# Start FPS Throughput Estimator
fps = FPS().start()

# Loop over frames
while True:
    frame = vs.read()
    frame = imutils.resize(frame, width = 600)
    (h, w) = frame.shape[:2]
    
    imageBlob = cv2.dnn.blobFromImage(cv2.resize(frame, (300, 300)), 1.0, (300, 300), (104.0, 177.0, 123.0), swapRB = False, crop = False)
    detector.setInput(imageBlob)
    
    detections = detector.forward()
    
    for i in range(0, detections.shape[2]):
        confidence = detections[0, 0, i, 2]

        if (confidence > 0.2):
            box = detections[0, 0, i, 3:7] * np.array([w, h, w, h])
            (startX, startY, endX, endY) = box.astype("int")
            
            face = frame[startY: endY, startX: endX]
            (fH, fW) = face.shape[:2]

            if ((fW < 20) or (fH < 20)):
                continue

            faceBlob = cv2.dnn.blobFromImage(face, 1.0/255, (96, 96), (0, 0, 0), swapRB = True, crop = False)

            embedder.setInput(faceBlob)

            vec = embedder.forward()
            # print(vec)

            preds = recognizer.predict_proba(vec)[0]
            j = np.argmax(preds)
            proba = preds[j]
            name = le.classes_[j]
            
            text = "{}: {:.2f}%".format(name, proba * 100)
            y = startY - 10 if (startY - 10 > 10) else (startY + 10)
            cv2.rectangle(frame, (startX, startY), (endX, endY), (0, 0, 255), 2)
            cv2.putText(frame, text, (startX, y), cv2.FONT_HERSHEY_SIMPLEX, 0.45, (0, 0, 255), 2)
        
    fps.update()
    cv2.imshow("Frame", frame)

    key = cv2.waitKey(1) & 0xFF
    if (key == ord('q') or key == ord('Q')):
        break

fps.stop()

print("Elapsed time: {:.2f}".format(fps.elapsed()))
print("Approx. FPS: {:.2f}".format(fps.fps()))

cv2.destroyAllWindows()
vs.stop()

Starting video stream...

[[ 1.20971859e-01  7.48845488e-02 -8.31057131e-02  3.50771137e-02
  -3.95287015e-03  2.70334721e-01  8.65767524e-02  1.28138559e-02
  -1.36145204e-03 -9.28848386e-02  1.12343803e-01  7.22044483e-02
   7.84580410e-02 -1.86147764e-01 -3.65087241e-02 -6.11171089e-02
  -1.12558581e-01  7.49163097e-03 -9.62576792e-02  7.18782693e-02
   1.44843876e-01 -1.78996716e-02 -1.24744903e-02  1.13946669e-01
   5.54275280e-03 -1.26462027e-01 -6.50308430e-02 -1.91299245e-01
  -3.48431729e-02  1.29393339e-01  3.24611627e-02 -2.12407950e-02
  -6.50765821e-02  1.19459189e-01  6.77935686e-03 -9.85254161e-03
  -3.45655647e-03 -4.34587076e-02 -8.57081788e-04  2.96407053e-03
   4.62494306e-02 -1.42835990e-01  1.52269867e-03  8.29970986e-02
  -1.07512973e-01 -1.64236695e-01  1.00726239e-01 -1.29287113e-02
  -1.25372857e-01  1.47671700e-01  5.26062064e-02 -5.88708445e-02
  -5.19313700e-02  5.92098981e-02  4.22744602e-02  4.38096188e-02
  -1.12799749e-01  9.75593179e-02 -6.87985867e-02 

[[-0.05563366  0.11673645 -0.0518994  -0.03491137 -0.0646706   0.15631609
  -0.07700327  0.01346725 -0.00813063  0.02117428  0.06883344 -0.03386329
   0.11899899 -0.10411014 -0.00651391  0.02191669 -0.15249544 -0.03770765
   0.01301952  0.04359315  0.19431193 -0.09948085  0.02151503  0.03374206
   0.04633439  0.0320274  -0.04627618 -0.22307886  0.07049995  0.11065213
   0.07365836 -0.00771035  0.06855182  0.02260972  0.02889249  0.03074785
   0.00535995  0.09276133  0.06236064 -0.03071896  0.01530301 -0.18881519
   0.00461786  0.07907183 -0.05000259 -0.07765358  0.17450763 -0.02364509
  -0.13931638 -0.07318859 -0.02487451  0.02380812  0.07289466  0.05995027
   0.0814091   0.08100495  0.05879483 -0.03215979 -0.01631305 -0.23695168
  -0.10311534 -0.07060809  0.14030506 -0.07920155  0.02168335  0.04193692
   0.04827221 -0.00182873  0.01366172 -0.05298921 -0.06153636 -0.0044237
  -0.1623481  -0.11797672  0.15780592 -0.00209558 -0.11175871  0.03623198
   0.03113751  0.23999998 -0.07380395 -

   0.09604774  0.09957075]]
[[-5.60444826e-03  9.86067951e-02 -1.82460900e-02  4.03605588e-03
  -2.83810440e-02  1.77501723e-01 -2.58858278e-02  2.96118809e-03
  -1.10356444e-02 -4.98594530e-02  5.32902330e-02  9.26329847e-03
   9.36759561e-02 -1.72404334e-01 -2.50263605e-02  1.41814360e-02
  -1.78510502e-01 -4.40444686e-02 -4.04002257e-02  7.23635107e-02
   2.22597420e-01 -1.03554107e-01  2.80689150e-02  8.16926137e-02
   6.71343356e-02 -2.89519317e-02 -6.58324882e-02 -2.33564883e-01
   4.57284600e-02  1.25808537e-01  8.40534791e-02 -2.52732895e-02
   2.21325718e-02  6.30586818e-02  3.82435471e-02 -4.54594567e-03
  -2.27847509e-02  5.46568334e-02  4.00741845e-02 -5.22240177e-02
   2.86011714e-02 -2.00970888e-01  3.53267938e-02  9.76582468e-02
  -4.31847908e-02 -9.21998918e-02  1.72760442e-01 -3.18405852e-02
  -1.48061827e-01  9.17330105e-03  5.58314787e-05 -1.98955983e-02
   4.40212376e-02  4.38004211e-02  9.95673314e-02  5.49646951e-02
  -2.52505695e-03  1.66587383e-02 -3.77198197e-0

   0.01494254  0.04572763]]
[[ 0.01243452  0.08345321 -0.04799277 -0.02153645 -0.00895937  0.1292293
   0.05363499  0.05053862 -0.04480481  0.00531026  0.04789721  0.01873333
   0.14740235 -0.16731153 -0.04035037  0.00542202 -0.16662885 -0.02731843
  -0.11411127  0.14735802  0.19272532 -0.16769761  0.03042339  0.07717097
   0.00649524 -0.02986031 -0.11082765 -0.21623339  0.07123983  0.09518446
   0.02746045  0.03388307 -0.01553917  0.08295941 -0.02971452 -0.03268952
  -0.05137209  0.12377522 -0.0065472  -0.05741792  0.03956668 -0.20541753
   0.01933761  0.11182322 -0.08009693 -0.09882701  0.1573849   0.00251569
  -0.15289097  0.0452431  -0.00997324 -0.04834141 -0.05073706  0.03921172
   0.09177089  0.01874301 -0.04467326  0.04508565 -0.01817141 -0.18046884
  -0.07497562 -0.05786566  0.15774621 -0.07325636  0.02447855 -0.01323521
  -0.00458117 -0.05680851 -0.0787437  -0.07055022 -0.06816003  0.04128347
  -0.11487395  0.00351159  0.08328051 -0.03149238 -0.01831265  0.04030125
   0.063352

   0.11494764  0.01927685]]
[[ 0.0707014   0.14583036 -0.0109506  -0.03051158  0.00983827  0.28717092
   0.07141055  0.00538834 -0.06867079 -0.06974787  0.03053496  0.05244541
   0.08144552 -0.17586413  0.00708482 -0.03545531 -0.12973008 -0.03581313
  -0.14536579  0.09239709  0.08478008  0.03007812 -0.02729029  0.03846847
  -0.0583228  -0.03592581 -0.1366257  -0.13458247  0.01752608  0.05362375
   0.03238666  0.06619501 -0.09661587  0.13334356 -0.00478559  0.03584952
   0.03234708  0.01075144  0.00615089  0.02793188  0.10558312 -0.14958219
   0.03316398  0.03341058 -0.11836096 -0.06167716  0.16117665 -0.00746881
  -0.20987493  0.12184453  0.03710201 -0.06258083 -0.09628163  0.0767685
   0.07128046  0.02756905 -0.11321881  0.11563335 -0.0596609  -0.09194849
  -0.13407385  0.04869486  0.18078241 -0.23302782  0.07053442 -0.00615524
   0.06349903 -0.07414345 -0.1860281   0.02759392  0.0008936   0.04536152
  -0.04183331  0.09593574  0.06769221  0.00803518 -0.0169892  -0.03305979
   0.044379

...

[[ 0.07267756  0.07276303  0.00155455  0.07103206  0.00188412  0.2888373
   0.04666871 -0.01876124  0.01822981 -0.07561492  0.1053817   0.05124051
   0.02248132 -0.19387262 -0.01813157  0.00881836 -0.1226215  -0.0078728
  -0.08115169  0.0378025   0.16313615 -0.0572147  -0.01453814  0.13562335
   0.06616605 -0.06571321 -0.10124794 -0.18594514  0.03438533  0.05809611
   0.14069057  0.02737905 -0.09384809  0.10810612  0.01934773  0.04296426
  -0.04066282 -0.02092648  0.0659332  -0.01849696  0.07175805 -0.14122526
  -0.03299484  0.01069615 -0.02293205 -0.184064    0.0953961  -0.01789559
  -0.1372152   0.05570573  0.00777515 -0.00863163 -0.00401115  0.00255629
   0.04498771  0.06292058 -0.0865664   0.13024229 -0.09725645 -0.08230398
  -0.14282857  0.00696498  0.22427389 -0.25505197  0.07185756  0.03785243
   0.06046123 -0.09170333 -0.18939053  0.08133825 -0.05147621  0.08949257
  -0.13026923  0.05094292  0.03382077 -0.06546964  0.03990345 -0.00974416
   0.00424632  0.18737681 -0.06614071 -0

   4.83190157e-02  8.97526741e-02  9.94332954e-02  2.09385063e-02]]
[[ 0.08803681  0.08212262 -0.04359882  0.03878786  0.03753145  0.3058373
   0.05195334 -0.02775374 -0.06311878 -0.03245725  0.08318835  0.03973803
   0.07408533 -0.16169956 -0.01954715  0.00870005 -0.09083295  0.02808705
  -0.06120775  0.07539188  0.16783696 -0.08763468  0.01565548  0.09845189
   0.04569655 -0.04586126 -0.14102678 -0.20292774  0.06686892  0.06852031
   0.09758158  0.06041893 -0.11863727  0.08389224  0.0245853   0.03886956
  -0.05161373  0.02236298  0.09161697 -0.04936207  0.05263644 -0.13319717
  -0.04452171  0.00344748 -0.0796661  -0.14370818  0.11865526  0.00778864
  -0.16943711  0.03942345  0.00540644  0.00494716 -0.01781037  0.0130245
   0.02809637  0.0364242  -0.03442069  0.1412153  -0.08550233 -0.1009502
  -0.12329516  0.04217815  0.24574164 -0.2620982   0.08715423  0.05239346
   0.0429686  -0.04795453 -0.17781195  0.05716515 -0.03775309  0.10940994
  -0.12505944  0.05444867  0.02578629 -0.053841

[[ 0.08871137  0.04857336 -0.03207818  0.02556998  0.01165225  0.3019799
   0.07903197  0.00381577 -0.01777642 -0.07472743  0.06903801  0.05215782
   0.07499511 -0.20235284 -0.02909433 -0.01006094 -0.1532957   0.00142556
  -0.11898331  0.07342722  0.16278447 -0.05826727  0.01234008  0.1338662
  -0.00833574 -0.07186359 -0.13043669 -0.23231278  0.01567644  0.05936004
   0.08728179  0.02575312 -0.12466393  0.11708256  0.01910074  0.02957289
  -0.03996325  0.01855301  0.0167367  -0.00818906  0.0685013  -0.14102973
  -0.05306154  0.03908122 -0.07055474 -0.15631463  0.10941906  0.00993503
  -0.15114161  0.10338949  0.00614718 -0.07136036 -0.03175747  0.02851124
   0.05343467  0.04240274 -0.06333449  0.14590444 -0.07055184 -0.09461299
  -0.11608409  0.04411311  0.2300631  -0.24215406  0.07779293 -0.01396607
   0.05381328 -0.07730357 -0.16542614  0.0464144  -0.05281001  0.08583245
  -0.09996253  0.06666149  0.0171687  -0.04982097  0.011978   -0.01400393
   0.04283073  0.1724847  -0.03698743 -0

   0.13076457  0.02615367]]
[[ 0.07860297  0.10330628 -0.04645364  0.02045487 -0.02134054  0.26238474
   0.01393405  0.01162856 -0.02168507 -0.10363345  0.08170359  0.05579797
   0.04670446 -0.2290891  -0.08825096  0.02947034 -0.15666784 -0.03922501
  -0.08582442  0.09405206  0.1904821  -0.04515401  0.02436725  0.08411755
  -0.00101125 -0.04495992 -0.05859834 -0.20777696  0.02804757  0.08455109
   0.04219054 -0.04067675 -0.04082881  0.11004519  0.0129015  -0.00669189
  -0.01016547  0.03297228  0.02537604 -0.00497502  0.00290838 -0.15118003
   0.02183511  0.06772599 -0.04530326 -0.13417594  0.1648965  -0.04687203
  -0.18381608  0.14242433  0.03139267 -0.02727993 -0.05212062  0.0723377
   0.07864852  0.02248383 -0.0329108   0.07479464 -0.07825803 -0.12554573
  -0.09949652 -0.01684843  0.24360278 -0.20480812  0.06992501 -0.07302867
   0.02578306 -0.09174833 -0.13996775  0.04744302 -0.05249837  0.03900781
  -0.11921571  0.03329491  0.05214337 -0.037283    0.01575269  0.01747772
   0.009104

[[ 0.06647249  0.09765279 -0.06458616 -0.00168508 -0.00476981  0.22205575
   0.03499382  0.03919849 -0.0613829  -0.08434574  0.06801253  0.0683251
   0.07137391 -0.25088093 -0.11492649  0.04093825 -0.13977396  0.00375994
  -0.11896536  0.10732938  0.19804311 -0.05438508  0.00365457  0.04696938
  -0.03431721 -0.03164004 -0.05436042 -0.21549992  0.01962424  0.09223413
  -0.02424246 -0.0093747  -0.03043902  0.1085163   0.00301478 -0.05070869
  -0.00658558  0.02672202 -0.00117721 -0.01222851  0.01820016 -0.15828593
   0.0577101   0.11112044 -0.05923238 -0.09252031  0.19560608 -0.0674547
  -0.23465513  0.11094831  0.0494342  -0.09649209 -0.09679225  0.07881151
   0.05191338  0.01507139 -0.04756702  0.04072526 -0.06430008 -0.11172924
  -0.04196016 -0.02743237  0.21049197 -0.15453437  0.0959686  -0.12151538
  -0.01094928 -0.09305926 -0.11284898 -0.00134513 -0.05472502  0.00381689
  -0.08629128 -0.00301312  0.03013249 -0.00577272  0.00233142  0.05678092
  -0.00861725  0.14085636 -0.04757302 -0